# Transfer File (AmazonS3)

With this notebook you can transfer an offered file for which you already have an Agreement to an `AmazonS3` storage.

## Preperation

Here some values are initialized that will be necessary for the other steps.


### Set up

Import the requests module and assign the base url of the Dataspace as a variable.

In [ ]:
from pprint import pprint
import requests

base_url = "https://api.adsel.space"

### Fill in Values

Fill in the values for the variables below.

In [ ]:
# Your JWT recevied from Keycloak via sso.adsel.space
token = "ey..."
token_header = {"Authorization": f"Bearer {token}"}
# The name of your Connector
connector_name = "my-connector"
# The URL of your AmazonS3 storage
aws_url = "https://s3.us-east-1.amazonaws.com"
# The region of your AmazonS3 storage
aws_region = "us-east-1"
# The username (Access Key ID) of your AmazonS3 storage account
aws_username = "my-access-key-id"
# The password (Secret Access ID) of your AmazonS3 storage account
aws_password = "my-secret-access-key"
# The bucket where the file should be stored in
aws_bucket = "my-bucket"
# The DSP address of the Connector providing the offer
originator = "https://api.adsel.space/connectors/alice/dsp"
# The ID of the Agreement for the offer
agreement_id = "some-random-uuid"

## Initiate Transfer

Here you will request for the transfer of the data to your storage.

Initiates the Transfer.

In [ ]:
url = f"{base_url}/backend/connectors/{connector_name}/management/v3/transferprocesses"
payload = {
  "@context": {
    "odrl": "http://www.w3.org/ns/odrl/2/"
  },
  "counterPartyAddress": originator,
  "contractId": agreement_id,
  "transferType": "AmazonS3-PUSH",
  "dataDestination": {
    "type": "AmazonS3",
    "region": aws_region,
    "endpointOverride": aws_url,
    "accessKeyId": aws_username,
    "secretAccessKey": aws_password,
    "bucketName": aws_bucket,
    "keyName": "dummy"
  },
  "protocol": "dataspace-protocol-http"
}

response = requests.post(url, json=payload, headers=token_header)
print(response.content)
response.raise_for_status()

transfer_id = response.json()["@id"]
print(f"Started Transfer with ID: {transfer_id}")

Confirms that the Transfer succeeded.

In [ ]:
url = f"{base_url}/backend/connectors/{connector_name}/management/v3/transferprocesses/{transfer_id}"

response = requests.get(url, headers=token_header)
response.raise_for_status()
print(f"Transfer data:\n")
pprint(response.json())

If everything was successful the file should now be in your storage.